# Get data from HuggingFace

In [ ]:
!pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 5.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 388.9/388.9 kB 8.7 MB/s eta 0:00:00
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.20.3
    Uninstalling huggingface-hub-0.20.3:
      Successfully uninstalled huggingface-hub-0.20.3


In [ ]:
from datasets import load_dataset
from google.colab import userdata
userdata.get('HF_TOKEN')

iNat = load_dataset('ba188/iNaturalist_v2')

Generating train split:   0%|          | 0/863 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/216 [00:00<?, ? examples/s]

In [ ]:
import numpy as np
import pandas as pd

np.array(list(iNat['train']['embedding'][0].split(',')))

inat_train = pd.DataFrame(iNat['train'])
inat_train['embedding'] = [np.array(list(x.split(','))) for x in inat_train['embedding']]

inat_test = pd.DataFrame(iNat['test'])
inat_test['embedding'] = [np.array(list(x.split(','))) for x in inat_test['embedding']]

In [ ]:
inat_train['embedding'][1].shape

(2048,)

# Define Goal and Create/Train Model(s)

Originally, wanted to try to replicate their model that can classify at the species level but because of API constraints and filtering, only have 1,079 observations with 413 unique species represented so may change the goal to be classifying at a higher taxonomic level (plant/animal/fungi/aves).


In [ ]:
def count_unique_strings(input_list):
    # Convert the list to a set to remove duplicates
    unique_strings = set(input_list)

    # Return the number of unique strings
    return len(unique_strings)

count_unique_strings(inat_train['species_guess'])

413

In [ ]:
import tensorflow as tf
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.ensemble import RandomForestClassifier
from operator import le
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()

### Try species-level classification

In [ ]:
inat_train = inat_train.dropna(subset=['location'])
inat_test = inat_test.dropna(subset=['location'])

# try to do species-level classification
X_train = inat_train['embedding']
X_train_array = np.array(X_train.tolist())
X_train_numeric = pd.to_numeric(X_train_array.flatten())
X_train_numeric = X_train_numeric.reshape(X_train_array.shape)

X_test = inat_test['embedding']
X_test_array = np.array(X_test.tolist())
X_test_numeric = pd.to_numeric(X_test_array.flatten())
X_test_numeric = X_test_numeric.reshape(X_test_array.shape)

# encode all possible ys
y_train_species = inat_train['species_guess'].to_numpy()
y_test_species = inat_test['species_guess'].to_numpy()

ys_species = y_train_species.tolist() + y_test_species.tolist()
ys_species = list(set(ys_species))
le = LabelEncoder()
le.fit(ys_species)
ys_species_encoded = le.transform(ys_species)

# split back into train and test by matching indices
y_train_species = [ys_species_encoded[ys_species.index(label)] for label in y_train_species]
y_test_species = [ys_species_encoded[ys_species.index(label)] for label in y_test_species]

#### ResNet50 Embedding + Logistic Regression


In [ ]:
# ResNet50 Embedding + Logistic Regression
# train logistic regression model
logreg_embed_species = LogisticRegression(max_iter=1000, multi_class='multinomial', solver='lbfgs', random_state=42)
logreg_embed_species.fit(X_train_numeric, y_train_species)

# evaluate accuracy
y_pred_train = logreg_embed_species.predict(X_train_numeric)
print("Accuracy on training data:", accuracy_score(y_train_species, y_pred_train))

y_pred_test = logreg_embed_species.predict(X_test_numeric)
print("Accuracy on testing data:", accuracy_score(y_test_species, y_pred_test))

Accuracy on training data: 0.9456906729634003
Accuracy on testing data: 0.7242990654205608


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [ ]:
print(inat_test.iloc[2]['photo'])
print(inat_test.iloc[2]['species_guess'])
print(le.inverse_transform(logreg_embed_species.predict(X_test_numeric[2].reshape(1,-1))))
print(le.inverse_transform(y_test_species[2].reshape(1,-1)))

https://inaturalist-open-data.s3.amazonaws.com/photos/33149746/square.jpg
Simulium
['Simulium']
['Simulium']


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


#### ResNet50 Embedding + Random Forest Classifier

In [ ]:
# Random Forest
# create and train a random forest model
rf_embed_species = RandomForestClassifier(n_estimators=100, random_state=42)
rf_embed_species.fit(X_train_numeric, y_train_species)

# evaluate accuracy
y_pred_train = rf_embed_species.predict(X_train_numeric)
print("Accuracy on training data:", accuracy_score(y_train_species, y_pred_train))

y_pred_test = rf_embed_species.predict(X_test_numeric)
print("Accuracy on testing data:", accuracy_score(y_test_species, y_pred_test))

Accuracy on training data: 0.9456906729634003
Accuracy on testing data: 0.719626168224299


In [ ]:
print(inat_test.iloc[2]['photo'])
print(inat_test.iloc[2]['species_guess'])
print(le.inverse_transform(rf_embed_species.predict(X_test_numeric[2].reshape(1,-1))))
print(le.inverse_transform(y_test_species[2].reshape(1,-1)))

https://inaturalist-open-data.s3.amazonaws.com/photos/33149746/square.jpg
Simulium
['Simulium']
['Simulium']


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


### Kingdom-level Classification

In [ ]:
# try to do kingdom-level classification
# encode all possible ys
y_train_taxa = inat_train['taxon'].to_numpy()
y_test_taxa = inat_test['taxon'].to_numpy()

ys_taxa = y_train_taxa.tolist() + y_test_taxa.tolist()
ys_taxa = list(set(ys_taxa))
le = LabelEncoder()
le.fit(ys_taxa)
ys_taxa_encoded = le.transform(ys_taxa)

y_train_taxa = [ys_taxa_encoded[ys_taxa.index(label)] for label in y_train_taxa]
y_test_taxa = [ys_taxa_encoded[ys_taxa.index(label)] for label in y_test_taxa]

#### ResNet50 Embedding + Logistic Regression

In [ ]:
# ResNet50 Embedding + Logistic Regression
# train logistic regression model
logreg_embed_taxa = LogisticRegression(max_iter=1000, multi_class='multinomial', solver='lbfgs', random_state=42)
logreg_embed_taxa.fit(X_train_numeric, y_train_taxa)

# evaluate accuracy
y_pred_train = logreg_embed_taxa.predict(X_train_numeric)
print("Accuracy on training data:", accuracy_score(y_train_taxa, y_pred_train))

y_pred_test = logreg_embed_taxa.predict(X_test_numeric)
print("Accuracy on testing data:", accuracy_score(y_test_taxa, y_pred_test))

Accuracy on training data: 1.0
Accuracy on testing data: 0.9813084112149533


In [ ]:
print(inat_test.iloc[2]['photo'])
print(inat_test.iloc[2]['taxon'])
print(le.inverse_transform(logreg_embed_taxa.predict(X_test_numeric[2].reshape(1,-1))))
print(le.inverse_transform(y_test_taxa[2].reshape(1,-1)))

https://inaturalist-open-data.s3.amazonaws.com/photos/33149746/square.jpg
Insecta
['Insecta']
['Insecta']


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


#### ResNet50 Embedding + Random Forest Classifier

In [ ]:
# Random Forest
# create and train a random forest model
rf_embed_taxa = RandomForestClassifier(n_estimators=100, random_state=42)
rf_embed_taxa.fit(X_train_numeric, y_train_taxa)

# evaluate accuracy
y_pred_train = rf_embed_taxa.predict(X_train_numeric)
print("Accuracy on training data:", accuracy_score(y_train_taxa, y_pred_train))

y_pred_test = rf_embed_taxa.predict(X_test_numeric)
print("Accuracy on testing data:", accuracy_score(y_test_taxa, y_pred_test))

Accuracy on training data: 1.0
Accuracy on testing data: 0.9626168224299065


In [ ]:
print(inat_test.iloc[2]['taxon'])
print(le.inverse_transform(rf_embed_taxa.predict(X_test_numeric[2].reshape(1,-1))))
print(le.inverse_transform(y_test_taxa[2].reshape(1,-1)))

Insecta
['Insecta']
['Insecta']


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


# Improve Model? - Weight by location


## Create Location Model(s)


In [ ]:
inat_train = inat_train.dropna(subset=['location'])
inat_test = inat_test.dropna(subset=['location'])

# reformat locations
locX_train = inat_train['location'].str.split(',', expand=True)
locX_train.columns = ['latitude', 'longitude']
locX_train['latitude'] = pd.to_numeric(locX_train['latitude'])
locX_train['longitude'] = pd.to_numeric(locX_train['longitude'])

locX_test = inat_test['location'].str.split(',', expand=True)
locX_test.columns = ['latitude', 'longitude']
locX_test['latitude'] = pd.to_numeric(locX_test['latitude'])
locX_test['longitude'] = pd.to_numeric(locX_test['longitude'])


### Species-level classification

#### Logistic Regression


In [ ]:
# logistic regression model based on locations
logreg_location_species = LogisticRegression(max_iter=100000, multi_class='multinomial', solver='lbfgs', random_state=42)
logreg_location_species.fit(locX_train, y_train_species)

# evaluate accuracy
y_pred_train = logreg_location_species.predict(locX_train)
print("Accuracy on training data:", accuracy_score(y_train_species, y_pred_train))

y_pred_test = logreg_location_species.predict(locX_test)
print("Accuracy on testing data:", accuracy_score(y_test_species, y_pred_test))

Accuracy on training data: 0.2632821723730815
Accuracy on testing data: 0.17289719626168223


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of f AND g EVALUATIONS EXCEEDS LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [ ]:
print(inat_test.iloc[2]['species_guess'])
print(le.inverse_transform(logreg_location_species.predict(locX_test.iloc[2].values.reshape(1,-1))))
print(le.inverse_transform(y_test_species[2].reshape(1,-1)))

Simulium
['Limnephilus']
['Simulium']


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


#### Random Forest

In [ ]:
# Random forest model based on locations
rf_location_species = RandomForestClassifier(n_estimators=100, random_state=42)
rf_location_species.fit(locX_train, y_train_species)

# evaluate accuracy
y_pred_train = rf_location_species.predict(locX_train)
print("Accuracy on training data:", accuracy_score(y_train_species, y_pred_train))

y_pred_test = rf_location_species.predict(locX_test)
print("Accuracy on testing data:", accuracy_score(y_test_species, y_pred_test))

Accuracy on training data: 0.910271546635183
Accuracy on testing data: 0.6915887850467289


In [ ]:
print(inat_test.iloc[2]['species_guess'])
print(le.inverse_transform(rf_location_species.predict(locX_test.iloc[2].values.reshape(1,-1))))
print(le.inverse_transform(y_test_species[2].reshape(1,-1)))

Simulium
['Simulium']
['Simulium']


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


### Kindgom-level classification


#### Logistic Regression

In [ ]:
# logistic regression model based on locations
logreg_location_taxa = LogisticRegression(max_iter=10000, multi_class='multinomial', solver='lbfgs', random_state=42)
logreg_location_taxa.fit(locX_train, y_train_taxa)

# evaluate accuracy
y_pred_train = logreg_location_taxa.predict(locX_train)
print("Accuracy on training data:", accuracy_score(y_train_taxa, y_pred_train))

y_pred_test = logreg_location_taxa.predict(locX_test)
print("Accuracy on testing data:", accuracy_score(y_test_taxa, y_pred_test))

Accuracy on training data: 0.40731995277449823
Accuracy on testing data: 0.40654205607476634


In [ ]:
print(inat_test.iloc[2]['taxon'])
print(le.inverse_transform(logreg_location_taxa.predict(locX_test.iloc[2].values.reshape(1,-1))))
print(le.inverse_transform(y_test_taxa[2].reshape(1,-1)))

Insecta
['Plantae']
['Insecta']


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


#### Random Forest

In [ ]:
# Random forest model based on locations
rf_location_taxa = RandomForestClassifier(n_estimators=100, random_state=42)
rf_location_taxa.fit(locX_train, y_train_taxa)

# evaluate accuracy
y_pred_train = rf_location_taxa.predict(locX_train)
print("Accuracy on training data:", accuracy_score(y_train_taxa, y_pred_train))

y_pred_test = rf_location_taxa.predict(locX_test)
print("Accuracy on testing data:", accuracy_score(y_test_taxa, y_pred_test))

Accuracy on training data: 0.9881936245572609
Accuracy on testing data: 0.9205607476635514


In [ ]:
print(inat_test.iloc[2]['taxon'])
print(le.inverse_transform(rf_location_taxa.predict(locX_test.iloc[2].values.reshape(1,-1))))
print(le.inverse_transform(y_test_taxa[2].reshape(1,-1)))

Insecta
['Insecta']
['Insecta']


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


## Combine Embedding and Location Models


In [ ]:
def combined_model(embedding_model, location_model, data):
    # Embedding Model
    embeddings = data['embedding_numeric'].apply(pd.Series)
    embeddings = embeddings.to_numpy()
    embedding_predictions = embedding_model.predict(embeddings)

    if type (embedding_model) == LogisticRegression:
        embedding_weights = embedding_model.coef_
    elif type (embedding_model) == RandomForestClassifier:
        embedding_weights = embedding_model.feature_importances_
    else:
        embedding_weights = embedding_model.get_weights()


    # Location Model
    locations = data[['latitude', 'longitude']]
    location_predictions = location_model.predict(locations)

    if type (location_model) == LogisticRegression:
        location_weights = location_model.coef_
    elif type (location_model) == RandomForestClassifier:
        location_weights = location_model.feature_importances_
        #location_weights = np.tile(location_model.feature_importances_, (embedding_weights.shape[0], 1))
    else:
        location_weights = location_model.get_weights()


    # Combine using weighted average
    embedding_predictions = embedding_predictions.reshape(-1,1)
    expanded_embedding_predictions = np.repeat(embedding_predictions, embedding_weights.shape[0], axis=1)
    embedding_piece = np.matmul(expanded_embedding_predictions,embedding_weights)

    location_predictions = location_predictions.reshape(-1,1)
    expanded_location_predictions = np.repeat(location_predictions, location_weights.shape[0], axis=1)
    location_weights = location_weights.reshape(-1,1)
    expanded_location_weights = np.repeat(location_weights, embedding_weights.shape[1], axis=1)
    location_piece = np.matmul(expanded_location_predictions,expanded_location_weights)

    combined_predictions = embedding_piece + location_piece
    combined_predictions = np.around(combined_predictions[:, 0], 0).astype(int)
    combined_predictions = list(combined_predictions)

    return combined_predictions

### Evaluate Combined Model

#### Get data in right format for the combined model

In [ ]:
# Get data in the right format for the combined model
# Training Data
inat_train = inat_train.dropna(subset=['location'])

inat_train[['latitude', 'longitude']] = inat_train['location'].str.split(',', expand=True)
inat_train['latitude'] = pd.to_numeric(inat_train['latitude'])
inat_train['longitude'] = pd.to_numeric(inat_train['longitude'])

inat_train['embedding_array'] = inat_train['embedding'].apply(lambda x: np.array(eval(x)) if isinstance(x, str) else x)
inat_train['embedding_numeric'] = inat_train['embedding_array'].apply(lambda x: x.flatten() if isinstance(x, np.ndarray) else x)
inat_train['embedding_numeric'] = inat_train['embedding_numeric'].apply(lambda x: pd.to_numeric(x))

embedding_numeric_array = inat_train['embedding_numeric'].values
embedding_numeric_reshaped = embedding_numeric_array.reshape(inat_train['embedding_array'].shape)
inat_train['embedding_numeric'] = embedding_numeric_reshaped



array([1.194838  , 0.        , 0.1844602 , ..., 0.18166535, 1.1895064 ,
       0.29901576])

In [ ]:
# Testing Data
inat_test = inat_test.dropna(subset=['location'])

inat_test[['latitude', 'longitude']] = inat_test['location'].str.split(',', expand=True)
inat_test['latitude'] = pd.to_numeric(inat_test['latitude'])
inat_test['longitude'] = pd.to_numeric(inat_test['longitude'])

inat_test['embedding_array'] = inat_test['embedding'].apply(lambda x: np.array(eval(x)) if isinstance(x, str) else x)
inat_test['embedding_numeric'] = inat_test['embedding_array'].apply(lambda x: x.flatten() if isinstance(x, np.ndarray) else x)
inat_test['embedding_numeric'] = inat_test['embedding_numeric'].apply(lambda x: pd.to_numeric(x))

embedding_numeric_array = inat_test['embedding_numeric'].values
embedding_numeric_reshaped = embedding_numeric_array.reshape(inat_test['embedding_array'].shape)
inat_test['embedding_numeric'] = embedding_numeric_reshaped


#### Evaluate for species level

In [ ]:
image_model = logreg_embed_species
location_model = rf_location_species

combined_train_predictions = combined_model(image_model, location_model, inat_train)
combined_test_predictions = combined_model(image_model, location_model, inat_test)

print("Accuracy on training data:", accuracy_score(y_train_species, combined_train_predictions))
print("Accuracy on testing data:", accuracy_score(y_test_species, combined_test_predictions))

Accuracy on training data: 0.910271546635183
Accuracy on testing data: 0.6915887850467289


In [ ]:
# Example case
print(inat_test['photo'][2])
print(inat_test['species_guess'][2])
print(le.inverse_transform(combined_test_predictions[2].reshape(1,-1)))
print(le.inverse_tranform(y_test_species[2].reshape(1,-1)))

https://inaturalist-open-data.s3.amazonaws.com/photos/33149746/square.jpg
Simulium


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


ValueError: y contains previously unseen labels: [340]

#### Evaluate for higher order

In [ ]:
image_model = logreg_embed_taxa
location_model = rf_location_taxa

combined_train_predictions = combined_model(image_model, location_model, inat_train)
combined_test_predictions = combined_model(image_model, location_model, inat_test)

print("Accuracy on training data:", accuracy_score(y_train_taxa, combined_train_predictions))
print("Accuracy on testing data:", accuracy_score(y_test_taxa, combined_test_predictions))

Accuracy on training data: 0.9881936245572609
Accuracy on testing data: 0.9205607476635514


In [ ]:
print(inat_test['photo'][2])
print(inat_test['taxon'][2])
print(le.inverse_transform(combined_test_predictions[2].reshape(1,-1)))
print(le.inverse_transform(y_test_taxa[2].reshape(1,-1)))

https://inaturalist-open-data.s3.amazonaws.com/photos/33149746/square.jpg
Insecta
['Insecta']
['Insecta']


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:155: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
